# Berechnung von Eigenwerten mit PINVIT

**Autor:** Martin Rupp (aufbereitet von Arne Nägel)

In einem Gebiet $\Omega \subset \mathbb R^d$ sei folgendes Eigenwertproblem gegeben:
\begin{align}
\left(-\triangle + v(x) \right)u &= \lambda u  &\text{in } \partial \Omega\\
u&=0 &\text{auf } \partial \Omega
\end{align}
Diskretisiert man dies mit Finiten-Elementen, so ergibt sich das verallgemeinerte Eigenwertproblem
$$ A_h u_h = \lambda B u_h$$ 


In diesem Beispiel werden die kleinsten $N=5$ Eigenwerte mit dem PINVIT-Verfahren [1] berechnet. Als Vorkonditionierer kommt ein Mehrgitterverfahren zum Einsatz.

*Literatur:*
1. Knyazev, A., Neymeyr, K.: Gradient flow approach to geometric convergence analysis of preconditioned eigensolvers. SIAM J. Matrix Anal. 31, 621–628 (2009) [DOI: 10.1137/080727567](https://doi.org/10.1137%2F080727567)
2. Gang Bao · Guanghui Hu · Di Liu: Numerical Solution of the Kohn-Sham Equation by Finite Element Methods with an Adaptive Mesh Redistribution Technique. J Sci Comput (2013) 55:372–391 [DOI: 10.1007/s10915-012-9636-1](https://doi.org/10.1007/s10915-012-9636-1)



In [1]:
-- Load utility scripts (e.g. from from ugcore/scripts)
ug_load_script("ug_util.lua")
ug_load_script("util/refinement_util.lua")
-- ug_load_script("../modsim2/teaching_problems.lua")

-- initialize ug with the world dimension and the algebra type
InitUG(3, AlgebraType("CPU", 1));

* Initializing: paths... done, bridge... done, plugins... done                 *
Loading Plugin Lua Content from /Users/anaegel/Software/ug4-git/plugins/d3f/lua-include.lua


# Problembeschreibung
### Einlesen des Gebietes 

In [2]:
numRefs = 4 -- 7 

-- Load a domain without initial refinements.
-- Refine the domain (parallel redistribution is handled internally!)
local gridName = "laplace_sample_grid_3d.ugx" -- grid name
local requiredSubsets = {"Inner", "Boundary"}

dom = util.CreateDomain(gridName, 0, requiredSubsets)
util.refinement.CreateRegularHierarchy(dom, numRefs, true)

Loading Domain laplace_sample_grid_3d.ugx ... done.
Performing integrity check on domain ... done.

util.refinement: - refining level 0
util.refinement: - refining level 1
util.refinement: - refining level 2
util.refinement: - refining level 3


In [3]:
-- Create approximation space.
approxSpace = ApproximationSpace(dom)
approxSpace:add_fct("u", "Lagrange", 1)
approxSpace:init_levels()
approxSpace:init_top_surface()
approxSpace:print_statistic()

| ---------------------------------------------------------------------------- |
|  Number of DoFs (All Procs)                                                  |
|  Algebra: Block 1 (divide by 1 for #Index)                                   |
|                                                                              |
|    GridLevel   |       Domain |     0: Inner |  1: Boundary                  |
| ---------------------------------------------------------------------------- |
| (lev,    0)    |           27 |            1 |           26 |
| (lev,    1)    |          125 |           27 |           98 |
| (lev,    2)    |          729 |          343 |          386 |
| (lev,    3)    |         4913 |         3375 |         1538 |
| (lev,    4)    |        35937 |        29791 |         6146 |
| (lev,    0, g) |           27 |            1 |           26 |
| (lev,    1, g) |          125 |           27 |           98 |
| (lev,    2, g) |          729 |          343 |          386 |
| 

In [4]:
-- Some auxiliary functions.
clock = CuckooClock()
OrderLex(approxSpace, "x")    -- order vertices (and dofs) lexicographically

OrderLex: all 27 SORTED.
OrderLex: all 125 SORTED.
OrderLex: all 729 SORTED.
OrderLex: all 4913 SORTED.
OrderLex: all 35937 SORTED.
OrderLex: all 27 SORTED.
OrderLex: all 125 SORTED.
OrderLex: all 729 SORTED.
OrderLex: all 4913 SORTED.
OrderLex: all 35937 SORTED.
OrderLex: all 35937 SORTED.


In [5]:
-- Create discretization.
domainDisc = DomainDiscretization(approxSpace)
poissonDisc = DomainDiscretization(approxSpace)

### Aufsetzen des Eigenwertproblems


In [6]:
-- Hartree potential (electron-electron)
velectron = GridFunction(approxSpace)
velectron:set(0.0)

In [7]:
-- External potential (nucleus-electron)
local nucleiDesc = {
    { Z = 1, pos = {0.3, 0.4, 0.1}}
}

function myExtPotential(x, y, z, t)
   
    local sum = 0.0
    for i,nucleus in ipairs(nucleiDesc) do
        local mycontrib = 0.0
        local rx = (x-nucleus.pos[1]);
        local ry = (y-nucleus.pos[2]); 
        local rz = (z-nucleus.pos[3]); 
        local dist2 = rx*rx+ry*ry+rz*rz;  
        sum = sum - nucleus.Z/math.sqrt(dist2);
    end
    print ("Ext="..sum)
    return sum
end

In [8]:
-- Debug output
temp = GridFunction(approxSpace)
temp:set(0.0)
Interpolate("myExtPotential", temp, "u")
WriteGridFunctionToVTK(temp, "vext")

Ext=-1.9611613513818
Ext=-1.9611613513818
Ext=-1.1111111111111
Ext=-1.0482848367219
Ext=-1.280368799329
Ext=-3.0151134457776
Ext=-2.1821789023599
Ext=-1.5617376188861
Ext=-0.82760588860237
Ext=-0.92847669088526
Ext=-0.89087080637475
Ext=-1.2309149097933
Ext=-1.474419561549
Ext=-4.0824829046386
Ext=-1.3363062095621
Ext=-1.0783277320344
Ext=-1.0206207261597
Ext=-1.9611613513818
Ext=-1.6666666666667
Ext=-0.97128586235726
Ext=-0.74329414624717
Ext=-0.99503719020999
Ext=-1.5617376188861
Ext=-0.90909090909091
Ext=-1.1111111111111
Ext=-2.1821789023599
Ext=-0.99503719020999
Ext=-0.7881104062391
Ext=-1.4547859349066
Ext=-0.88648441435587
Ext=-0.83844361630064
Ext=-1.3834289277321
Ext=-1.6384638410381
Ext=-1.0140402531268
Ext=-2.8571428571429
Ext=-2.1199957600127
Ext=-2.4077170617154
Ext=-1.6384638410381
Ext=-1.9156525704423
Ext=-1.2194215216994
Ext=-0.96560909917053
Ext=-0.94385835636602
Ext=-0.72121844597462
Ext=-0.7120188545089
Ext=-0.81044089847311
Ext=-1.1026356928399
Ext=-0.78506867197886


In [9]:
disc = "fe"

local myElemDisc = ConvectionDiffusion("u", "Inner", disc)
myElemDisc:set_diffusion(0.5)

local veff=ScaleAddLinkerNumber()
veff:add(1.0, LuaUserNumber("myExtPotential"))       -- vext
veff:add(1.0, GridFunctionNumberData(velectron,"u")) -- vhartree
myElemDisc:set_reaction_rate(veff)
domainDisc:add(myElemDisc)

Ext=-1.9611613513818


In [10]:
-- b) Boundary
myDirichletBND = DirichletBoundary() 
myDirichletBND:add(0.0, "u", "Boundary")
domainDisc:add(myDirichletBND)

# Lösen des Eigenwertproblems

## Konfiguration des Mehrgitter-Vorkonditionierers

In [11]:
-- Create smoother. 
jac = Jacobi(0.66)             -- Jacobi (w/ damping)
gs  = GaussSeidel()            -- Gauss-Seidel (forward only)
sgs = SymmetricGaussSeidel()   -- Symmetric Gauss-Seidel (forward + backward)

In [12]:
local solverutil={}

solverDesc = 
{
    type = "linear",  -- linear solver type ["bicgstab", "cg", "linear"]
    precond = {
        type        = "gmg",    -- preconditioner ["gmg", "ilu", "ilut", "jac", "gs", "sgs"]
        smoother    = "gs",     -- gmg-smoother ["ilu", "ilut", "jac", "gs", "sgs"]
        cycle       = "V",      -- gmg-cycle ["V", "F", "W"]
        preSmooth   = 1,        -- number presmoothing steps
        postSmooth  = 1,        -- number postsmoothing steps
        rap         = true,    -- computes RAP-product instead of assembling if true 
        
        baseLevel   = 0,        -- gmg - baselevel
        baseSolver  = "lu",
    
        approxSpace = approxSpace,
        
    },
    convCheck = "standard"
}

-- Multigrid preconditioner for PINVIT
gmg = util.solver.CreatePreconditioner(solverDesc.precond)
gmg:set_discretization(domainDisc)

-- Multigrid solver 
lsolver = util.solver.CreateSolver(solverDesc, solverutil)
convCheck = solverutil.convCheckDescs[1].instance

## Konfiguration von PINVIT
Als Löser kommt eine inverse Iteration mit Vorkonditionierer (engl: *preconditioned inverse iteration, PINVIT*) zum Einsatz.

In [13]:
evNumber = 10

In [14]:
-- Define storage for eigenfunctions.
u = {}
for i=1,evNumber do
    u[i] = GridFunction(approxSpace)
    u[i]:set_random(-1.0, 1.0)
    domainDisc:adjust_solution(u[i]) -- Setze Randwerte
end

In [15]:
-- Define density as an (auxiliary) resulting quantity. 
rho = ScaleAddLinkerNumber()
for i=1,evNumber do
    phi = ExplicitGridFunctionValue(u[i], "u")
    rho:add(phi,phi)
end

In [16]:
-- Define matrix on left and right hand side
A = MatrixOperator()
domainDisc:assemble_stiffness_matrix(A, u[1])

B = MatrixOperator()
domainDisc:assemble_mass_matrix(B, u[1])

Ext=-0.83971281484451
Ext=-0.84156925399726
Ext=-0.81494879910754
Ext=-0.85370069338299
Ext=-0.82595016741278
Ext=-0.82771662436809
Ext=-0.82771662436809
Ext=-0.8283819737087
Ext=-0.802956306659
Ext=-0.83994419806095
Ext=-0.81347286154426
Ext=-0.81410442360327
Ext=-0.81179585545914
Ext=-0.81347286154426
Ext=-0.7883973849247
Ext=-0.82332155999067
Ext=-0.79735319365534
Ext=-0.79894210210836
Ext=-0.82310364051411
Ext=-0.82595016741278
Ext=-0.79974012668138
Ext=-0.83626485409244
Ext=-0.80909270353598
Ext=-0.81179585545914
Ext=-0.88095790178278
Ext=-0.88310226788784
Ext=-0.85370069338299
Ext=-0.89574378226291
Ext=-0.86510502961935
Ext=-0.86713543792674
Ext=-0.86713543792674
Ext=-0.86790053507678
Ext=-0.83994419806095
Ext=-0.87989156004742
Ext=-0.85079907950502
Ext=-0.85152170845059
Ext=-0.84888102695078
Ext=-0.85079907950502
Ext=-0.82332155999067
Ext=-0.86083734290089
Ext=-0.83240804654769
Ext=-0.83421635378185
Ext=-0.86183582069741
Ext=-0.86510502961935
Ext=-0.83626485409244
Ext=-0.8756645

In [17]:
-- Define PINVIT.
evIterations = 50  -- number of iterations of the eigenvalue solver
evPrec = 1e-3       -- precision of the eigenvalue solver
evKeep = 8

pinvit = EigenSolver()
pinvit:set_linear_operator_A(A)
pinvit:set_linear_operator_B(B)
pinvit:set_max_iterations(evIterations)
pinvit:set_precision(evPrec)
pinvit:set_preconditioner(gmg)
pinvit:set_pinvit(2) -- ?
pinvit:set_additional_eigenvectors_to_keep(evKeep)

-- Assign storage.
for i=1,evNumber do
    domainDisc:adjust_solution(u[i]) 
    pinvit:add_vector(u[i])
end

In [18]:
-- OPTIONAL: debug output
-- dbgWriter = GridFunctionDebugWriter(approxSpace)
-- pinvit:set_debug(dbgWriter)

## Aufruf des Lösers

In [19]:
-- Solve eigenvalue problem.
pinvit:apply()

PINVIT Eigensolver by Martin Rupp / G-CSC 2013-2015.
 MaxIterations = 50
 Precision = 0.001 (absolute) 
 MinimumDefectToCalcCorrection = 0.001
 Number of EV = 10
 PINVIT = 2 = Preconditioned Block Gradient Method
 Preconditioner: 
 | GeometricMultigrid (V-Cycle)
 |  Smoother (1x pre, 1x post): Gauss-Seidel( damping = ConstantDamping(1))
 |  Basesolver ( Baselevel = 0, gathered base = false): AgglomeratingSolver: SuperLU

	Additionaly storing 8 eigenvectors

Initializing... done.
PINVIT: Initializing preconditioner... done.
iteration 0
0 lambda:              1284.33 defect:              9.07139
1 lambda:              1277.54 defect:              9.15789
2 lambda:              1266.67 defect:              9.03909
3 lambda:              1272.09 defect:              9.19104
4 lambda:              1286.12 defect:              9.20827
5 lambda:              1267.13 defect:              9.16818
6 lambda:              1293.68 defect:              9.25691
7 lambda:               1268.3 defect: 

## Ausgaben und Post-Processing  

In [20]:
-- Print results.
for i=1,evNumber do
    WriteGridFunctionToVTK(u[i], "ev_"..i)
end

In [21]:
-- Print density.
myVTK = VTKOutput()
myVTK:select_element(rho, "density")
myVTK:print("density", u[1])

# Poissonlöser für  Elektron-Elektron-Wechselwirkungen
Die Elektron-Elektron-Wechselwirkungen ergeben sich aus der folgenden Äquivalenz: 
$$- \triangle u = f \text{ in } \mathbb R^3 $$
sowie
$$ u(x) = \frac{1}{4 \pi} \int_{\mathbb R^3} \frac{1}{|x-y|} f(y)\, dy$$

In [22]:
function PoissonSolver(u, rhs, solver, poissonDisc)
   
    -- Assemble linear system
    local clock = CuckooClock()
    local A = AssembledLinearOperator(poissonDisc)
    poissonDisc:assemble_linear(A, rhs)
    WriteGridFunctionToVTK(rhs, "rho")

    -- Call solver
    clock:tic()
    solver:init(A, u) -- boundary values
    solver:apply_return_defect(u,rhs)
    print ("Poisson solver: "..clock:toc().." seconds.")
end    

In [23]:
local myElemDisc = ConvectionDiffusion("u", "Inner", disc)
local fourPi = 4.0 *3.1415926535897932384626433832795028
myElemDisc:set_diffusion(1.0)
myElemDisc:set_source(4.0*rho)
poissonDisc:add(myElemDisc)

Es fehlen noch geeignete Randbedingungen:

In [24]:
poissonDisc:add(myDirichletBND)

Jetzt können wir das (aktualisierte) Hartree-Potential berechnen:

In [25]:
PoissonSolver(velectron, temp, lsolver, poissonDisc)


   % %%%%%%%%      Iterative Linear Solver      %%%%%%%%%%%
   % %%%%%%%%   (Precond: Geometric MultiGrid)  %%%%%%%%%%%
   %   Iter      Defect         Rate 
   %    0:    3.047618e-01      -------
   %    1:    4.246971e-02    1.393538e-01
   %    2:    3.898322e-03    9.179063e-02
   %    3:    2.686032e-04    6.890226e-02
   %    4:    1.925695e-05    7.169292e-02
   %    5:    1.233520e-06    6.405583e-02
   %    6:    1.079250e-07    8.749351e-02
   % Relative reduction 1.000000e-06 reached after 6 steps.
   % Average reduction over 6 steps: 8.411244e-02
   % %%%%%  Iteration converged  %%%%%

Poisson solver: 0.139351 seconds.


In [26]:
WriteGridFunctionToVTK(velectron, "velectron")